In [ ]:
"""
Please save notebooks with important results to your own folder in JupyterHub.
See README for usage instructions:
https://git.zooxlabs.com/zooxco/driving/tree/master/mined_metric/jupyter/README.md
"""
import pandas as pd

from mined_metric.jupyter.utils.data_access_util import get_experiment_data, chum_summary_stats
from mined_metric.jupyter.utils.visualization_util import (
    vis_metric_distribution,
    vis_velocity_time_series,
    vis_hero_state_time_series,
    vis_decision_state_time_series,
)

EXPERIMENT_ID = "EXPERIMENT_ID_PLACEHOLDER"

In [ ]:
def stuck_agg_metrics(filtered_meta_data):
    """ Calculate Stuck aggregate metrics for a subset of meta data

    Arguments:
        filtered_meta_data {list of dict} -- a filtered subset of meta data
    """
    num_cleared_events = 0
    num_stuck_events = 0
    total_time_to_clear_s = 0
    total_time_stuck_s = 0

    for chum in filtered_meta_data:
        if "time_stuck_s" in chum:
            if chum["cleared"]:
                num_cleared_events += 1
                total_time_to_clear_s += chum["time_stuck_s"]
            else:
                num_stuck_events += 1
                total_time_stuck_s += chum["time_stuck_s"]

    if num_cleared_events == 0:
        avg_time_to_clear_s = 0
    else:
        avg_time_to_clear_s = total_time_to_clear_s / num_cleared_events

    if num_stuck_events == 0:
        avg_time_stuck_s = 0
    else:
        avg_time_stuck_s = total_time_stuck_s / num_stuck_events

    return {
        "avg_time_to_clear_s": avg_time_to_clear_s,
        "avg_time_stuck_s": avg_time_stuck_s,
        "num_cleared_events": num_cleared_events,
        "num_stuck_events": num_stuck_events,
    }

In [ ]:
# Retrieve all experiment data and metadata
exp_data = get_experiment_data(EXPERIMENT_ID)
if "exception" in exp_data:
    print("Invalid data is returned: %s" % exp_data["exception"])

In [ ]:
# Calculate basic Chum URI summary statistics
chum_uris = [d["chum_uri"] for d in exp_data["meta"]]
stats = chum_summary_stats(chum_uris)
print("Average duration of Chum URIs: {:.2f}s".format(stats["avg_duration_s"]))
print("Vehicles: {}".format(stats["vehicles_included"]))

In [ ]:
# Calculate Stuck aggregate metrics
vehicles = ["kitt_10", "kitt_15", "kitt_20"]
for vehicle in vehicles:
    filtered_meta_data = [
      chum for chum in exp_data["meta"]
      if vehicle in chum["chum_uri"]
    ]
    agg_metrics = stuck_agg_metrics(filtered_meta_data)
    agg_metrics = pd.DataFrame(
        agg_metrics.items(),
        columns=["Metric", "Metric Value"],
    )
    agg_metrics = agg_metrics.set_index("Metric")
    print("Stuck aggregate metrics for %s:" % vehicle)
    print(agg_metrics)
    print("\n\n")

In [ ]:
# Visualize metric distributions
vis_metric_distribution(exp_data, ["time_stuck_s"])

In [ ]:
# Visualize velocity over time
vis_velocity_time_series(chum_uris[0])

In [ ]:
# Visualize roll, pitch, and yaw over time
vis_hero_state_time_series(chum_uris[0])

In [ ]:
# Visualize the decision state over time
vis_decision_state_time_series(chum_uris[0])